# Deploy & Upgrade using Helm Charts on K8s

Helm is a powerful package manager for Kubernetes, designed to simplify the process of deploying, managing, and configuring applications on Kubernetes clusters. By using Helm charts, developers and operations teams can define, install, and upgrade even the most complex Kubernetes applications with ease. 

This introduction will cover the basics of Helm charts, including prerequisites and an important feature: upgradeability via Helm.

If you are highly familiar with k8s, you can use directly the [helm chart available here](https://artifacthub.io/packages/helm/openmined/syft).

## Prerequisites

Before diving into Helm charts, ensure you have the following prerequisites in place:

1. **helm**: Install Helm on your local machine. The installation instructions for different operating systems are available on the [Helm official website](https://helm.sh/docs/intro/install/).

2. **kubectl**: The Kubernetes command-line tool, kubectl, should be installed and configured to interact with your Kubernetes cluster. You can download it from the Kubernetes official site: [Linux](https://kubernetes.io/docs/tasks/tools/install-kubectl-linux/), [MacOS](https://kubernetes.io/docs/tasks/tools/install-kubectl-macos/).

3. **Get familiar with Kubernetes**: A tutorial to present the basics is [available here](https://kubernetes.io/docs/tutorials/kubernetes-basics/).

4. **Access Rights**: Ensure you have sufficient permissions to create resources in the Kubernetes cluster and install Helm charts.

## Understanding Helm Charts
A Helm chart is a collection of files that describe a set of Kubernetes resources. Helm uses these charts to deploy applications or services on Kubernetes. Each chart contains the following essential components:

- `Chart.yaml`: This file contains metadata about the chart, such as the name, version, and description.
- `Values.yaml`: This file includes default values for the chart’s variables, which can be overridden by users during deployment.


## Server Deployment

### Step 1. Add Helm Repo

A Helm repository is a collection of packaged charts that can be shared and accessed publicly or privately. These repositories are similar to package repositories in other ecosystems, like npm for Node.js or PyPI for Python. Helm repositories make it easy to distribute charts and manage their versions.

To use a Helm repository, you need to add it to your local Helm client. Here we are adding PySyft's helm repository:


```bash
helm repo add openmined https://openmined.github.io/PySyft/helm
```

Make sure your repo is up to date before moving forward:

```bash
helm repo update openmined
```

### Step 2. Search for available Chart versions

You can search for available charts in the added repositories using the helm search command. For instance, to search for various versions of the Syft charts, you can use:


```bash
helm search repo openmined/syft --versions --devel
```

Adding `--devel` allows the search to include `beta` versions of syft.

### Step 3. Setup a registry

To setup a k8s deployment, you need a running Kubernetes cluster. This can be a local setup using tools like Minikube or a managed Kubernetes service such as Google Kubernetes Engine (GKE), Amazon EKS, or Azure Kubernetes Service (AKS).

We will cover here the setup of a local registry using k3d. First, we need to create the registry:


```bash
k3d registry create registry.localhost --port 12345  -v `pwd`/k3d-registry:/var/lib/registry || true
```

Now we can create the cluster for illustration purposes:

```bash
CLUSTER_NAME=syft SERVER_PORT=8080 && \
k3d cluster create CLUSTER_NAME -p "$SERVER_PORT:80@loadbalancer" --registry-use k3d-registry.localhost || true \
k3d cluster start CLUSTER_NAME
```

### Step 4. Install using Helm

To install a chart from a repository, use the helm install command along with the repository name and the chart name. 

First, we should set a version for deployment, as:

```bash
export SYFT_VERSION="<paste your version here>"
```


```bash
helm install my-server openmined/syft --version $SYFT_VERSION --namespace syft --create-namespace --set ingress.ingressClass=traefik
```

Depending on your cloud system, you can configure ingress differently. To pass a local `values.yaml` file, you can specify to the above:

```bash
 -f $PATH_TO_VALUES \
 --value_name $VALUE
```

## Upgrading your server using Helm

One of Helm’s key features is the ability to upgrade applications with minimal downtime and effort. Helm manages upgrades through a concept called "releases." Each time you install a chart, Helm creates a new release. When you upgrade a release, Helm performs a rolling update, applying the new configuration while keeping the application running.

### Steps to Upgrade a Helm Release

1. Update repository to have the latest versions & search

2. Modify Values: Update the values.yaml file or provide a new set of values that reflect the desired state of the application.

3. Upgrade Command: Use the helm upgrade command to apply the changes.

### Step 1. Update local repository


```bash
helm repo add openmined https://openmined.github.io/PySyft/helm

helm repo update openmined

helm search repo openmined/syft --versions --devel
```

### Step 2. Set the target version and release name


```bash
export TARGET_VERSION="<paste your target version>"

# User Defined
export RELEASE_NAME="<paste the release name>"
export NAMESPACE="<paste the namespace>"
helm get values $RELEASE_NAME -n $NAMESPACE -o yaml > values.yaml
```

### Step 3. Upgrade the Helm Chart

```bash

export PATH_TO_VALUES=usr/tmp/values.yaml

helm upgrade $RELEASE_NAME openmined/syft \
 --version $TARGET_VERSION \
 -f $PATH_TO_VALUES \
 --namespace $NAMESPACE
```

## Test your deployment

1. **Check ingress run**

To confirm the health of the ingress run: 

```bash
kubectl describe ingress -n syft
```

2. **Check running pods**

```bash
kubectl get pods -n syft
```

3. **Launch your Jupyter Notebook Instance**

In this step, you need a client server in order to interact with the PySyft server you just deployed. Here, the client consists of a Jupyter notebook running the same version of PySyft as the server served as a container. This is a convenient setup, but you can as well launch your own Jupyter Notebook in an environment with Python3.10+ and the desired PySyft version.

We need to start the client as follows:

```bash
docker run --rm -it --network=host openmined/syft-client:${VERSION}
```
where `${VERSION}` is the version of PySyft Client you’d like to run. It must be the same as you passed before at deployment step.

If this step is successful, you will be taken to a Jupyter notebook interface in the browser. Please create a new notebook and run the following command to test your full setup is ready to be used:

4. **Connect to your launched server**


In [ ]:
import syft as sy

sy.login(url="localhost:80", email="info@openmined.org", password="changethis")

 # Please pass the URL, the email and password used to create the server. The above are the default ones used during server creation.

If everything works well, you should be able to login to your server. You can now start running PySyft commands on the client server to interact with the PySyft server you just deployed.